# Lecture 19: Data Preparation and Transformation with pandas
## Building Complete Data Analysis Workflows

**Course:** INF 605 - Introduction to Programming - Python  
**Instructor:** Prof. Rongyu Lin  
**Institution:** Quinnipiac University

### Learning Objectives
By the end of this lecture, you will be able to:
1. Create DataFrames from dictionaries for data generation and testing
2. Save DataFrames to CSV files using to_csv() with proper parameters
3. Load external data by reading CSV files into DataFrames using pd.read_csv()
4. Filter data effectively using advanced boolean indexing techniques
5. Create computed columns through vectorized calculations and transformations
6. Group and aggregate data by categories using groupby()
7. Combine datasets by stacking multiple DataFrames with pd.concat()
8. Execute complete end-to-end data analysis workflows

### Prerequisites
This lecture builds on:
- Lecture 16: pandas Series (NaN, statistical methods, string operations)
- Lecture 17: pandas DataFrames (structure, indexing, boolean filtering)
- Lecture 18: Data Cleaning (missing data, duplicates, type conversion)
- Lectures 12-13: NumPy arrays and np.where() for conditional operations

## Setup and Imports

We need pandas for data manipulation and NumPy for functions like np.where() for conditional operations. Think of these as your complete data analysis toolkit - pandas handles data structures and file operations, NumPy provides mathematical and logical operations. The standard convention is importing as `pd` and `np`, universally recognized across the data science community.

In [ ]:
# Standard imports for data analysis workflows
import pandas as pd
import numpy as np

# Display library versions for reference
print(f"pandas version: {pd.__version__}")
print(f"NumPy version: {np.__version__}")

## Part 1: Creating and Working with CSV Files

### The Complete Data Workflow

Real-world data analysis follows a complete cycle: Create → Save → Load → Transform → Analyze → Save Results. Before we can read and analyze CSV files, we need to understand how data gets into CSV format in the first place. In this section, you'll learn both sides of the equation: creating DataFrames from scratch and saving them as CSV files, then loading them back for analysis.

CSV (Comma-Separated Values) files are the universal language of data exchange. They're simple text files where each line represents a row and commas separate column values. Almost every tool - Excel, databases, analytics platforms - can read and write CSV files, making them essential for data sharing and workflow automation.

### Creating Sample Data from Dictionaries

The foundation of pandas work is the DataFrame. While real projects load data from files or databases, you first need to understand how DataFrames are created. The most common approach uses Python dictionaries where keys become column names and values become column data. Think of it as defining your table structure programmatically - each key-value pair defines one column's name and all its values.

In [ ]:
# Create student test score data using dictionary structure
# Each key is a column name, each value is a list of column data

student_data = {
    'Student': ['Alice', 'Bob', 'Charlie', 'Diana', 'Eve', 'Frank', 'Grace',
                'Henry', 'Isabel', 'Jack', 'Kelly', 'Liam', 'Maya', 'Nathan',
                'Olivia', 'Paul', 'Quinn', 'Rachel', 'Sam', 'Tina', 'Uma',
                'Victor', 'Wendy', 'Xander', 'Yara'],
    'Test1': [92, 78, 85, 91, np.nan, 88, 76, 95, 82, np.nan, 89, 73, 94, 81,
              87, 72, 90, 84, 79, 93, 77, 86, 91, 74, 88],
    'Test2': [88, 82, 89, 94, np.nan, 85, 79, 92, 86, np.nan, 91, 75, 96, 83,
              89, np.nan, 88, 87, 81, 95, 78, 84, 93, 76, 90],
    'Test3': [91, 79, 87, 93, 75, 90, 77, 94, 84, 68, 88, 74, 95, 82,
              86, 71, 92, 85, 80, 94, 76, 88, 90, 73, 89],
    'Status': ['Active', 'Active', 'Active', 'Active', 'Inactive', 'Active',
               'Active', 'Active', 'Active', 'Inactive', 'Active', 'Inactive',
               'Active', 'Active', 'Active', 'Active', 'Active', 'Active',
               'Inactive', 'Active', 'Active', 'Active', 'Active', 'Inactive', 'Active']
}

# Convert dictionary to DataFrame
students_df = pd.DataFrame(student_data)

print("Created student records DataFrame:")
print(students_df.head(10))
print(f"\nShape: {students_df.shape}")
print(f"Columns: {students_df.columns.tolist()}")

**What Happened:** We created a DataFrame from a dictionary where each key-value pair defines one column. Notice how np.nan represents missing values (some students missed tests). The dictionary keys ('Student', 'Test1', etc.) became column names. All lists must have the same length - 25 students in this case. pd.DataFrame() automatically aligned everything into a table structure.

### Saving DataFrames to CSV Files

Once you have a DataFrame, save it to CSV using to_csv(). This converts your DataFrame into a text file where rows become lines and columns are separated by commas. The most important parameter is index=False, which prevents pandas from writing row numbers as an extra column. Without this, reloading the CSV creates an unwanted 'Unnamed: 0' column.

In [ ]:
# Save student data to CSV file
# index=False prevents writing row numbers as a column

students_df.to_csv('student_records.csv', index=False)
print("Saved student_records.csv")

# Verify the file was created by checking first few lines
print("\nFirst 5 lines of the CSV file:")
with open('student_records.csv', 'r') as f:
    for i, line in enumerate(f):
        if i < 5:
            print(line.strip())
        else:
            break

**What Happened:** to_csv() wrote our DataFrame to a text file. The first line contains column names (Student,Test1,Test2,Test3,Status). Each subsequent line is one student's data with commas separating values. Missing values appear as empty fields. This CSV file can now be opened in Excel, loaded by other programs, or shared with colleagues.

### Creating Multiple Related DataFrames

Real projects often involve multiple related datasets - monthly sales, quarterly reports, multi-location data. Let's create three months of sales data with identical structure but different values. This simulates receiving monthly export files from a sales system. We'll use the same product list but vary the units sold to show realistic month-to-month fluctuations.

In [ ]:
# Create January sales data
sales_jan_data = {
    'Product': ['Laptop', 'Mouse', 'Keyboard', 'Monitor', 'USB Cable', 'Webcam',
                'Headphones', 'Desk Lamp', 'Office Chair', 'Screwdriver Set',
                'External SSD', 'HDMI Cable', 'Power Strip', 'Wireless Router', 'Microphone'],
    'Category': ['Electronics', 'Accessories', 'Accessories', 'Electronics', 'Accessories',
                 'Electronics', 'Electronics', 'Hardware', 'Hardware', 'Hardware',
                 'Electronics', 'Accessories', 'Hardware', 'Electronics', 'Electronics'],
    'Units_Sold': [45, 156, 132, 67, 203, 89, 124, 78, 34, 145, 92, 187, 98, 56, 73],
    'Price_Per_Unit': [899.99, 15.99, 45.50, 249.99, 8.99, 79.99, 59.99, 34.99,
                       189.99, 24.99, 129.99, 12.99, 19.99, 89.99, 99.99]
}

sales_jan_df = pd.DataFrame(sales_jan_data)
print("January sales data:")
print(sales_jan_df.head())

In [ ]:
# Create February sales data (same products, different units sold)
sales_feb_data = sales_jan_data.copy()
sales_feb_data['Units_Sold'] = [52, 167, 141, 71, 219, 95, 138, 82, 41, 152, 98, 195, 105, 63, 79]

sales_feb_df = pd.DataFrame(sales_feb_data)

# Create March sales data (same products, different units sold)
sales_mar_data = sales_jan_data.copy()
sales_mar_data['Units_Sold'] = [58, 174, 149, 76, 228, 101, 145, 87, 38, 159, 104, 203, 112, 68, 84]

sales_mar_df = pd.DataFrame(sales_mar_data)

print("Created three months of sales data")
print(f"January: {len(sales_jan_df)} products")
print(f"February: {len(sales_feb_df)} products")
print(f"March: {len(sales_mar_df)} products")

In [ ]:
# Save all three months to separate CSV files
sales_jan_df.to_csv('sales_jan.csv', index=False)
sales_feb_df.to_csv('sales_feb.csv', index=False)
sales_mar_df.to_csv('sales_mar.csv', index=False)

print("Saved three CSV files:")
print("- sales_jan.csv")
print("- sales_feb.csv")
print("- sales_mar.csv")
print("\nEach file contains the same 15 products with different monthly sales figures")

**What Happened:** We created three DataFrames with identical structure (same columns, same products) but different Units_Sold values simulating monthly variation. Saving each to separate CSV files mimics real business scenarios where you receive periodic data exports. These files have consistent structure, making them perfect for combining later with pd.concat().

### Reading and Inspecting CSV Files

Now that we've created and saved CSV files, let's load them back. The pd.read_csv() function reads CSV files into DataFrames. It's remarkably smart - automatically detecting headers, inferring data types (integers, floats, strings), and handling missing values. This is where the workflow cycle continues: files you or others create become inputs for analysis.

In [ ]:
# Load student records CSV file
students = pd.read_csv('student_records.csv')

print("Loaded student_records.csv:")
print(students.head())      # preview first rows
print("\nDataFrame info:")
print(students.info())      # structure and types
print(f"\nShape: {students.shape}")  # (rows, columns)

**What Happened:** pd.read_csv() read the CSV file and recreated our DataFrame exactly as we saved it. The head() method shows first 5 rows for quick inspection. info() reveals 25 entries, 5 columns, data types (float64 for Test scores allowing NaN, object for strings), and which columns have missing values. The shape tuple (25, 5) means 25 rows and 5 columns. Always use these methods immediately after loading to verify data integrity.

### Useful read_csv() Parameters

pd.read_csv() has many parameters for handling different CSV formats and optimizing loading. Three most useful: index_col sets a column as the index for faster lookups, usecols loads only specified columns to save memory with large files, dtype forces specific data types when pandas inference is wrong.

In [ ]:
# Use Student column as index for easier lookup
students_indexed = pd.read_csv('student_records.csv', index_col='Student')
print("With Student as index:")
print(students_indexed.head())

# Load only specific columns to save memory
subset = pd.read_csv('student_records.csv', usecols=['Student', 'Test1', 'Status'])
print("\nLoading only selected columns:")
print(subset.head())
print(f"Shape: {subset.shape} (only 3 columns instead of 5)")

### Filtering with Boolean Masks

Boolean masks are True/False arrays matching DataFrame row count. They filter rows by creating conditions that evaluate to True/False for each row. Only rows where the mask is True are kept. Masks can be saved to variables, combined with logical operators, and reused. This is more readable and flexible than complex single-line filters.

In [ ]:
# Create boolean masks (True/False for each row)
has_test1 = students['Test1'].notna()  # True where Test1 is not NaN
is_active = students['Status'] == 'Active'  # True where Status is 'Active'

print("has_test1 mask (first 10):")
print(has_test1.head(10))

print("\nis_active mask (first 10):")
print(is_active.head(10))

# Use masks to filter DataFrame
active = students[is_active]
print(f"\nActive students: {len(active)} out of {len(students)}")

# Combine masks with & (AND operator)
complete = students[is_active & has_test1]
print(f"Active students with Test1 score: {len(complete)}")

**What Happened:** has_test1 mask is True for rows where Test1 exists (not NaN). is_active mask is True for Active students. Applying mask students[is_active] returns only rows where mask is True. Combining masks with & (AND) requires both conditions True. Use & (AND), | (OR), ~ (NOT) for complex logic. Always use parentheses around each condition when combining: (condition1) & (condition2).

### Complex Multi-Condition Filtering

Real analysis often requires multiple simultaneous conditions - active students with scores above thresholds, products in price ranges with high sales, data within date ranges meeting quality criteria. Combine multiple conditions with & (AND), | (OR), and ~ (NOT). Parentheses around each condition are mandatory - without them, operator precedence causes errors.

In [ ]:
# Filter for high-performing active students
high_perf = students[
    (students['Status'] == 'Active') &
    (students['Test1'] > 85) &
    (students['Test2'] > 85)
]

print("High-performing active students:")
print(high_perf[['Student', 'Test1', 'Test2', 'Status']])
print(f"\nFound {len(high_perf)} students meeting all criteria")

### Exercise 1: Loading and Filtering Sales Data

Practice loading CSV files and applying filters. Using the sales_jan.csv file:
1. Load the dataset with Product as the index
2. Add a Revenue column (Units_Sold * Price_Per_Unit)
3. Filter to show only products with Revenue > 5000
4. Display Product name, Units_Sold, Price_Per_Unit, and Revenue for filtered results

In [ ]:
# Your code here - load sales_jan.csv and filter by revenue


In [ ]:
# Solution
sales = pd.read_csv('sales_jan.csv', index_col='Product')

# Add Revenue column
sales['Revenue'] = sales['Units_Sold'] * sales['Price_Per_Unit']

# Filter for high revenue products
high_revenue = sales[sales['Revenue'] > 5000]

print("High revenue products (Revenue > $5000):")
print(high_revenue[['Units_Sold', 'Price_Per_Unit', 'Revenue']])
print(f"\nFound {len(high_revenue)} products with revenue > $5000")

## Part 2: Creating Computed Columns

### Vectorized Calculations for New Columns

Computed columns transform raw data into meaningful metrics using vectorized operations that process entire columns at once. When you write df['Total'] = df['Test1'] + df['Test2'] + df['Test3'], pandas adds columns element-wise for all rows simultaneously - milliseconds even for millions of rows. This is dramatically faster and clearer than loops. Computed columns are fundamental for deriving business metrics.

In [ ]:
# Load student test scores
students = pd.read_csv('student_records.csv')

# Create total score column (vectorized operation)
students['Total'] = (students['Test1'] + 
                     students['Test2'] + 
                     students['Test3'])

print("Students with Total score:")
print(students[['Student', 'Test1', 'Test2', 'Test3', 'Total']].head())

In [ ]:
# Create percentage column
max_score = 300
students['Percentage'] = (students['Total'] / max_score) * 100

print("With percentage scores:")
print(students[['Student', 'Total', 'Percentage']].head())

In [ ]:
# Create average score column
students['Average'] = students[['Test1', 'Test2', 'Test3']].mean(axis=1)

print("With average scores:")
print(students[['Student', 'Average']].head())

**What Happened:** We created three computed columns using vectorized operations. Total sums the three tests (NaN propagates if any test missing). Percentage converts to 0-100 scale. Average uses mean(axis=1) which automatically ignores NaN values. These columns are now permanent parts of the DataFrame.

### Conditional Column Creation with np.where()

NumPy's np.where() provides vectorized conditional operations: np.where(condition, value_if_true, value_if_false). This is incredibly powerful for creating categorical columns based on numeric thresholds. Want Pass/Fail based on scores? Use np.where(df['Score'] >= 70, 'Pass', 'Fail'). For multiple conditions, nest np.where() calls.

In [ ]:
# Load data and calculate totals
students = pd.read_csv('student_records.csv')
students['Total'] = (students['Test1'] + 
                     students['Test2'] + 
                     students['Test3'])

# Create Pass/Fail column
students['Result'] = np.where(students['Total'] >= 210, 'Pass', 'Fail')

print("Students with Pass/Fail status:")
print(students[['Student', 'Total', 'Result']])

In [ ]:
# Create letter grade column with nested np.where()
students['Percentage'] = (students['Total'] / 300) * 100

students['Grade'] = np.where(students['Percentage'] >= 90, 'A',
                    np.where(students['Percentage'] >= 80, 'B',
                    np.where(students['Percentage'] >= 70, 'C',
                    np.where(students['Percentage'] >= 60, 'D', 'F'))))

print("Students with letter grades:")
print(students[['Student', 'Percentage', 'Grade']])

**What Happened:** First np.where() created Pass/Fail based on Total >= 210. Nested np.where() created letter grades through cascading checks (A if >= 90, else B if >= 80, etc.). Students with NaN totals get NaN grades - np.where() preserves missing values.

### Exercise 2: Creating Computed Columns

Using sales_jan.csv, create these computed columns:
1. Revenue column (Units_Sold * Price_Per_Unit)
2. Volume_Category column: 'High' if Units_Sold >= 100, else 'Low'
3. Price_Category column: 'Budget' if Price < 20, 'Mid' if 20-30, 'Premium' if > 30
4. Calculate total revenue across all products

In [ ]:
# Your code here - create the computed columns


In [ ]:
# Solution - Load data and create Revenue
sales = pd.read_csv('sales_jan.csv')

# 1. Revenue column
sales['Revenue'] = sales['Units_Sold'] * sales['Price_Per_Unit']
print("Sales data with Revenue:")
print(sales[['Product', 'Units_Sold', 'Price_Per_Unit', 'Revenue']].head())

# 2. Volume_Category column
sales['Volume_Category'] = np.where(sales['Units_Sold'] >= 100,
                                    'High', 'Low')
print("\nWith Volume Category:")
print(sales[['Product', 'Units_Sold', 'Volume_Category']].head())

# 3. Price_Category column
sales['Price_Category'] = np.where(sales['Price_Per_Unit'] < 20,
                                   'Budget',
                          np.where(sales['Price_Per_Unit'] <= 30,
                                   'Mid', 'Premium'))
print("\nWith Price Category:")
print(sales[['Product', 'Price_Per_Unit', 'Price_Category']].head())

# 4. Total revenue
total_revenue = sales['Revenue'].sum()
print(f"\nTotal January revenue: ${total_revenue:,.2f}")

## Part 3: Grouping and Aggregation with groupby()

### Understanding the GroupBy Concept

Grouping implements the split-apply-combine pattern: split DataFrame into groups based on categories, apply aggregation functions to each group, combine results into summary DataFrame. This transforms detailed data into actionable insights. If you have 1000 students across 20 majors and group by Major, you get 20 rows showing average values per major. This condensation is the essence of business intelligence.

### Basic Groupby with Single Aggregation

The simplest groupby groups by one column and applies one aggregation: df.groupby('category')['value'].function(). Common functions include mean(), sum(), count(), min()/max(), and std(). The size() method counts records per group, showing whether groups are balanced or imbalanced.

In [ ]:
# Load sales data
sales = pd.read_csv('sales_jan.csv')

# Group by Category, calculate total units sold
category_units = sales.groupby('Category')['Units_Sold'].sum()

print("Total units sold by category:")
print(category_units)

In [ ]:
# Group by Category, count products
category_count = sales.groupby('Category').size()

print("Number of products per category:")
print(category_count)

In [ ]:
# Group by Category, calculate average price
category_price = sales.groupby('Category')['Price_Per_Unit'].mean()

print("Average price per category:")
print(category_price)

**What Happened:** Each groupby condensed our dataset into category-level summaries. First summed units sold per category. size() count revealed products per category. mean() price showed Electronics average $29.99 while Hardware averages $19.99. Category column became the index in results.

### Multiple Aggregations with agg()

The agg() method lets you specify multiple aggregation functions at once. Pass a list ['sum', 'mean', 'count'] to apply same aggregations to one column, or pass a dictionary to apply different aggregations to different columns. This creates comprehensive multi-metric summaries.

In [ ]:
# Multiple statistics for one column
sales = pd.read_csv('sales_jan.csv')

category_stats = sales.groupby('Category')['Units_Sold'].agg([
    'sum',   # Total units
    'mean',  # Average units per product
    'count'  # Number of products
])

print("Units sold statistics by category:")
print(category_stats)

In [ ]:
# Different aggregations for different columns
category_summary = sales.groupby('Category').agg({
    'Units_Sold': 'sum',
    'Price_Per_Unit': 'mean'
})

print("Comprehensive category summary:")
print(category_summary)

**What Happened:** First aggregation with list ['sum', 'mean', 'count'] created three columns showing total, average, and count per category. Dictionary-based aggregation applied different functions to different columns (sum for units, mean for price), producing clean two-column summary.

### Exercise 3: Groupby Analysis

Using student_records.csv, perform these groupby analyses:
1. Group by Status, calculate average Test1 score for each status
2. Group by Status, count how many students in each status
3. Group by Status, calculate sum, mean, and count of Test2 scores
4. Find which status group has higher average Test1 scores

In [ ]:
# Your code here - perform the groupby analyses


In [ ]:
# Solution - Load data and perform analyses
students = pd.read_csv('student_records.csv')

# 1. Average Test1 by Status
status_test1 = students.groupby('Status')['Test1'].mean()
print("Average Test1 by Status:")
print(status_test1)

# 2. Count students by Status
status_count = students.groupby('Status').size()
print("\nStudent count by Status:")
print(status_count)

# 3. Multiple statistics for Test2 by Status
status_test2 = students.groupby('Status')['Test2'].agg([
    'sum', 'mean', 'count'
])
print("\nTest2 statistics by Status:")
print(status_test2)

# 4. Which status has higher average Test1?
higher_status = status_test1.idxmax()
higher_score = status_test1.max()
print(f"\nStatus with higher Test1 average: {higher_status}")
print(f"Average score: {higher_score:.2f}")

## Part 4: Combining DataFrames with pd.concat()

### Understanding Concatenation

Concatenation means stacking DataFrames vertically (adding rows) or horizontally (adding columns). Vertical concatenation (axis=0) is most common for combining data from multiple time periods or files with identical column structure. Unlike merging/joining, concat doesn't match on keys - it just stacks data in order.

### Vertical Concatenation - Stacking Rows

When you have multiple datasets with identical structure, vertical concatenation combines them by stacking rows. The pd.concat() function takes a list of DataFrames and stacks them in order. The result row count equals the sum of input row counts. All data is preserved with original row indices maintained.

In [ ]:
# Load three months of sales data
jan_sales = pd.read_csv('sales_jan.csv')
feb_sales = pd.read_csv('sales_feb.csv')
mar_sales = pd.read_csv('sales_mar.csv')

print("January sales:")
print(jan_sales)
print(f"Shape: {jan_sales.shape}")

In [ ]:
# Concatenate all three months vertically
q1_sales = pd.concat([jan_sales, feb_sales, mar_sales])

print("Q1 sales (all three months combined):")
print(q1_sales)
print(f"\nJan: {len(jan_sales)} rows")
print(f"Feb: {len(feb_sales)} rows")
print(f"Mar: {len(mar_sales)} rows")
print(f"Q1 total: {len(q1_sales)} rows (sum of all three)")

**What Happened:** We loaded three CSV files (15 products each) with identical structure. pd.concat() stacked them vertically, preserving all 45 rows. Notice index goes 0-14, 0-14, 0-14 - original indices preserved, creating duplicates. All data present - Laptop appears three times (once per month).

### Resetting Index After Concatenation

After stacking, use ignore_index=True to renumber rows continuously (0, 1, 2, ..., N) instead of preserved duplicates. This creates clean sequential index. Use when indices have no business meaning and you want clean numbering.

In [ ]:
# Load monthly data
jan = pd.read_csv('sales_jan.csv')
feb = pd.read_csv('sales_feb.csv')

# Concatenate WITHOUT index reset
combined_old = pd.concat([jan, feb])
print("Without ignore_index:")
print(combined_old.index.tolist())
print("Notice: 0-14 from Jan, then 0-14 from Feb (duplicates!)")

In [ ]:
# Concatenate WITH index reset
combined_new = pd.concat([jan, feb], ignore_index=True)
print("\nWith ignore_index=True:")
print(combined_new.index.tolist())
print("Clean sequence: 0-29 with no duplicates")

**What Happened:** Without ignore_index, index has duplicates [0,1,2,...,14,0,1,2,...,14]. With ignore_index=True, index becomes clean sequential [0,1,2,...,29]. Both contain same data, only index differs.

### Exercise 4: Concatenating DataFrames

Practice combining multiple DataFrames:
1. Load sales_jan.csv, sales_feb.csv, and sales_mar.csv
2. Concatenate all three with ignore_index=True
3. Group the combined data by Product, sum Units_Sold to get quarterly totals
4. Find which product had the highest total quarterly sales

In [ ]:
# Your code here - complete the concatenation and analysis


In [ ]:
# Solution 
# 1: Load all three months
jan = pd.read_csv('sales_jan.csv')
feb = pd.read_csv('sales_feb.csv')
mar = pd.read_csv('sales_mar.csv')
print("Loaded three monthly files")

# 2: Concatenate with index reset
q1_sales = pd.concat([jan, feb, mar], ignore_index=True)
print("Q1 combined sales:")
print(f"Total rows: {len(q1_sales)}")

# 3: Group by Product, sum units
quarterly_totals = q1_sales.groupby('Product')['Units_Sold'].sum()
print("\nQuarterly sales by product:")
print(quarterly_totals)

# 4: Find top product
top_product = quarterly_totals.idxmax()
top_units = quarterly_totals.max()
print(f"\nTop product: {top_product}")
print(f"Units sold in Q1: {top_units}")

## Part 5: Saving Results to CSV

### Exporting DataFrames with to_csv()

After loading, cleaning, transforming, and analyzing, save results with to_csv() so others can use them, you can continue work later, or import into other tools. This completes the workflow cycle: CSV → DataFrame → analysis → new CSV. Saving intermediate results is good practice - save cleaned data so you don't repeat work.

In [ ]:
# Create processed student data
students = pd.read_csv('student_records.csv')

# Add computed columns
students['Total'] = (students['Test1'] + 
                     students['Test2'] + 
                     students['Test3'])
students['Average'] = students[['Test1', 'Test2', 'Test3']].mean(axis=1)

# Save processed data
students.to_csv('students_processed.csv')
print("Saved to students_processed.csv")

In [ ]:
# Verify by loading back
verify = pd.read_csv('students_processed.csv')
print("Loaded back processed file:")
print(verify.head())
print(f"\nColumns: {verify.columns.tolist()}")

**What Happened:** We saved processed DataFrame with computed columns to CSV. Loading back verifies success. Notice extra 'Unnamed: 0' column - this is the default integer index that to_csv() wrote. Usually not desired.

### Controlling CSV Output with Parameters

The most important parameter is index, which controls whether row index gets written. By default (index=True), pandas writes index as first column, creating unwanted extra column when reloading. Use index=False to exclude index and keep CSV clean with only data columns.

In [ ]:
# Create summary data
sales = pd.read_csv('sales_jan.csv')
summary = sales.groupby('Category').agg({
    'Units_Sold': 'sum',
    'Price_Per_Unit': 'mean'
})

print("Summary DataFrame:")
print(summary)

In [ ]:
# Save WITHOUT index (recommended)
summary.to_csv('category_summary_clean.csv', index=False)
print("Saved without index")

# Save WITH index
summary.to_csv('category_summary_with_index.csv')
print("Saved with index")

In [ ]:
# Load both to compare
clean = pd.read_csv('category_summary_clean.csv')
with_index = pd.read_csv('category_summary_with_index.csv')

print("Loaded WITHOUT index:")
print(clean)
print(f"Columns: {clean.columns.tolist()}")

print("\nLoaded WITH index:")
print(with_index)
print(f"Columns: {with_index.columns.tolist()}")

**What Happened:** File saved with index=False loads cleanly with just data columns. File with default settings has extra 'Category' column from index. Generally, index=False produces cleaner, more portable CSV files.

## Part 6: Complete End-to-End Workflow

### Real-World Scenario - Student Performance Analysis

Let's build a complete workflow demonstrating everything: loading from CSV, exploring, cleaning, filtering, creating computed columns, grouping, and saving. Scenario: analyze student performance to identify honors program qualifiers (Active status, complete test data, average > 87). We'll break into logical steps, documenting decisions and checking results - professional data science practice.

### Step 1-2: Load and Explore Data

Load data and immediately explore its structure. Use head() to inspect visually, info() to see types and missing values, describe() for statistical summaries. Never skip exploration - datasets change, exports might be incomplete, corruption happens. This reveals issues and guides cleaning decisions.

In [ ]:
# STEP 1: Load data
print("="*60)
print("STEP 1: Loading student data from CSV")
print("="*60)
students = pd.read_csv('student_records.csv')
print(f"Loaded {len(students)} student records")

In [ ]:
# STEP 2: Explore structure
print("\n" + "="*60)
print("STEP 2: Exploring data structure")
print("="*60)
print(f"Shape: {students.shape}")
print("\nFirst few rows:")
print(students.head())

print("\nData types and missing values:")
print(students.info())

print("\nMissing value counts:")
print(students.isna().sum())

**Exploration Results:** Loaded 25 students with 5 columns. Status complete, but test scores have various missing values. Mix of Active and Inactive students. We'll need to filter for Active status and handle missing scores.

### Step 3-4: Filter and Create Computed Columns

Transform data for analysis. Step 3 filters to relevant subset (Active students with complete test data). Step 4 creates computed columns deriving meaningful metrics (Total and Average scores). These transformations prepare data specifically for our analytical question.

In [ ]:
# STEP 3: Filter to relevant subset
print("\n" + "="*60)
print("STEP 3: Filtering to active students with complete data")
print("="*60)

active_complete = students[
    (students['Status'] == 'Active') &
    (students['Test1'].notna()) &
    (students['Test2'].notna()) &
    (students['Test3'].notna())
]

print(f"Filtered to {len(active_complete)} students")
print(f"Removed {len(students) - len(active_complete)} students")

In [ ]:
# STEP 4: Create computed columns
print("\n" + "="*60)
print("STEP 4: Creating performance metrics")
print("="*60)

active_complete['Total'] = (active_complete['Test1'] + 
                            active_complete['Test2'] + 
                            active_complete['Test3'])

active_complete['Average'] = active_complete[['Test1', 'Test2', 'Test3']].mean(axis=1)

print("Added columns: Total, Average")
print("\nStudents with performance metrics:")
print(active_complete[['Student', 'Total', 'Average']])

**Transformation Results:** Filtering reduced dataset to students meeting criteria. Added Total and Average columns through vectorized calculations. These computed metrics will be basis for final honors program filter.

### Step 5-6: Final Analysis and Results

Perform final analytical steps. Step 5 applies honors threshold (Average > 87) and creates results DataFrame. Step 6 sorts by performance (descending Average) to present top performers first, making report useful for stakeholders.

In [ ]:
# STEP 5: Apply honors threshold
print("\n" + "="*60)
print("STEP 5: Identifying honors program qualifiers")
print("="*60)

honors_eligible = active_complete[active_complete['Average'] > 87]

print(f"Students qualifying: {len(honors_eligible)}")
print(f"Qualification rate: {len(honors_eligible)/len(active_complete)*100:.1f}%")

In [ ]:
# STEP 6: Sort and format final results
print("\n" + "="*60)
print("STEP 6: Creating final report")
print("="*60)

final_report = honors_eligible.sort_values('Average', ascending=False)
report_columns = ['Student', 'Test1', 'Test2', 'Test3', 'Average']
final_report = final_report[report_columns]

print("Honors Program Eligible Students:")
print(final_report)

**Analysis Results:** Identified students qualifying for honors program (Active, complete data, average > 87). Results sorted by performance to highlight top performers. Report ready for stakeholders.

In [ ]:
# STEP 7: Save final results
print("\n" + "="*60)
print("STEP 7: Saving results to CSV")
print("="*60)

final_report.to_csv('honors_eligible_students.csv', index=False)
print("Saved: honors_eligible_students.csv")

active_complete.to_csv('students_all_processed.csv', index=False)
print("Saved: students_all_processed.csv")

In [ ]:
print("\n" + "="*60)
print("WORKFLOW COMPLETE!")
print("="*60)
print(f"Analyzed {len(students)} initial students")
print(f"Filtered to {len(active_complete)} active students with complete data")
print(f"Identified {len(honors_eligible)} honors program qualifiers")
print("\nResults saved and ready for review")

**Workflow Complete:** This demonstrated complete professional workflow: Load → Explore → Filter → Transform → Analyze → Save. Started with raw CSV data, systematically applied criteria, saved results. This systematic approach ensures reproducibility, transparency, and reliability.

## Summary and Key Takeaways

### What You Learned

You mastered the complete data preparation and transformation workflow:

1. **Reading CSV Files:** Use pd.read_csv() with parameters (index_col, usecols, dtype)
2. **Advanced Filtering:** Create reusable boolean masks and chain conditions with &, |, ~
3. **Computed Columns:** Use vectorized operations and np.where() for conditional logic
4. **Grouping:** Use groupby() with aggregation functions (sum, mean, count)
5. **Combining DataFrames:** Stack with pd.concat(), using ignore_index=True
6. **Saving Results:** Export with to_csv(), using index=False for clean output
7. **Complete Workflows:** Execute Load → Explore → Clean → Transform → Analyze → Save

### Best Practices

- Always inspect after loading with head(), info(), describe()
- Use named boolean masks for complex filtering
- Leverage vectorized operations (never loops)
- Check groupby results make sense
- Use ignore_index=True after concatenating
- Save with index=False for clean CSV files
- Document workflow decisions

### Next Steps

Future topics build on this foundation:
- Merging and joining DataFrames on key columns
- Pivot tables and reshaping for multi-dimensional analysis
- Time series operations with datetime indices
- Data visualization with matplotlib and seaborn

The workflow pattern you mastered - Load → Explore → Clean → Transform → Analyze → Save - remains constant regardless of complexity. You now have the fundamental toolkit of professional data analysts.